# 1. BERTopic： 使用预训练模型做话题建模


**用pandas读取数据，这里使用 pd.read_json 方法读取 JSON 文件，指定 orient='records' 和 lines=True 以匹配 JSON Lines 格式。**


In [2]:
import pandas as pd

df = pd.read_json('data/people_daily_news/2023_converted.json', orient='records', lines=True)

# 显示 DataFrame 的列名
print(df.columns)

# 保留指定的列
df = df[['title', 'text']]

# 显示前几行数据
print(df.head())


Index(['date', 'title', 'page', 'text'], dtype='object')
                                      title  \
0                        国家主席习近平发表二〇二三年新年贺词   
1                中俄两国元首互致新年贺电\n中俄两国总理互致新年贺电   
2  《求是》杂志发表习近平总书记重要讲话\n为实现党的二十大确定的目标任务而团结奋斗   
3                习近平向拉马福萨当选连任南非非洲人国民大会主席致贺电   
4    今天的中国，是梦想接连实现的中国\n——习近平主席二〇二三年新年贺词启示录①   

                                                text  
0  　　■ 2022年，我们胜利召开党的二十大，擘画了全面建设社会主义现代化国家、以中国式现代化...  
1  　　新华社北京12月31日电  2022年12月31日，国家主席习近平和俄罗斯总统普京互致新...  
2  　　新华社北京12月31日电  2023年1月1日出版的第1期《求是》杂志将发表中共中央总书...  
3  　　新华社北京12月31日电  12月31日，中共中央总书记习近平致电祝贺拉马福萨当选连任南...  
4  　　日月开新元，万象启新篇。告别2022年，迎来2023年，时间再次刻印下我们前行的坐标。\...  


# 2. 数据清洗
**这里定义了一个清洗数据函数clean_text，使用 re 包的sub函数，来替换字符串中匹配正则表达式的部分。它的基本用法如下：**
`re.sub(pattern, repl, string, count=0, flags=0)`

>  参数说明
>- pattern：要匹配的正则表达式模式。
>- repl：用于替换的字符串或函数。
>- string：要处理的原始字符串。
>- count：可选参数，指定替换的最大次数，默认值为 0，表示替换所有匹配的部分。
>- flags：可选参数，指定匹配时的标志，比如 re.IGNORECASE 表示忽略大小写。

**用jieba来进行分词。**

需要注意BERTopic需要先将中文分词改造成类似英文文本格式（用空格间隔词语）

In [3]:
import re
import jieba
import cntext as ct

stopwords = ct.load_pkl_dict('STOPWORDS.pkl')['STOPWORDS']['chinese']

def clean_text(text):
    """
    清理文本，去除中英文字符、数字及常见标点。

    参数:
    text (str): 需要清理的原始文本。

    返回:
    str: 清理后的文本。
    """
    # 定义了一个正则表达式，用于匹配所有非中英文字符、数字及常见标点的字符。
    pattern = r'[^\u4e00-\u9fa5A-Za-z0-9.,;!?()"\']' 
    
    # 将 text 中所有匹配 pattern 的字符替换为空字符串，即删除这些字符。
    cleaned_text = re.sub(pattern, "", text)
    
    # 将 cleaned_text 中的多个连续空白字符替换为单个空格。
    cleaned_text = re.sub(r"\s+", " ", cleaned_text)  
    
    # 去除首尾空白
    cleaned_text = cleaned_text.strip()  
    
    cleaned_text = jieba.lcut(cleaned_text)
    
    #过滤掉停用词。
    cleaned_text = [w for w in cleaned_text if w not in stopwords]
    return ' '.join(cleaned_text)



test = "云南永善县级地震已致人伤间民房受损中新网月日电据云南昭通市防震减灾局官方网站消息截至日时云南昭通永善县级地震已造成人受伤其中重伤人轻伤人已全部送医院救治民房受损户间倒塌户间个乡镇所学校不同程度受损目前被损毁电力交通通讯设施已全部抢通修复当地已调拨帐篷顶紧急转移万人月日时分云南昭通永善县发生里氏级地震震源深度公里当地震感强烈此外成都等四川多地也有明显震感"

clean_text(test)


Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\ZHONGH~1\AppData\Local\Temp\jieba.cache
Loading model cost 0.891 seconds.
Prefix dict has been built successfully.


'云南 永善县 级 地震 已致 伤间 民房 受损 中新网 日电 云南 昭通市 防震 减灾 局 官方网站 消息 日时 云南 昭通 永善县 级 地震 造成 受伤 重伤 轻伤 送 医院 救治 民房 受损 户间 倒塌 户间 乡镇 学校 不同 程度 受损 目前 损毁 电力 交通 通讯 设施 抢通 修复 调拨 帐篷 顶 紧急 转移 万人 时分 云南 昭通 永善县 发生 里氏 级 地震 震源 深度 公里 震感 强烈 成都 四川 多地 明显 震感'

In [5]:
df['content'] = df['text'].apply(clean_text)
print(df.head())
# 将处理好的daraframe保存为csv
df.to_csv('/data/output.csv', index=False, encoding='utf-8')

# 下次直接读
# df = pd.read_csv('data/output.csv')

# 由于数据多这里只取前1000个
df = df.head(1000)
print(df)

                                                 title  \
0                                   国家主席习近平发表二〇二三年新年贺词   
1                           中俄两国元首互致新年贺电\n中俄两国总理互致新年贺电   
2             《求是》杂志发表习近平总书记重要讲话\n为实现党的二十大确定的目标任务而团结奋斗   
3                           习近平向拉马福萨当选连任南非非洲人国民大会主席致贺电   
4               今天的中国，是梦想接连实现的中国\n——习近平主席二〇二三年新年贺词启示录①   
..                                                 ...   
995                            本版责编：管璇悦  陈圆圆  曹雪盟  陈世涵   
996  苏州挖潜存量资源化解老城区停车矛盾——\n车位错时共享  提升周转效率（一线探民生·解决停车难②）   
997                                  应急管理部提示做好寒潮天气防范应对   
998                                       重庆优化调整低保认定条件   
999                                        广州试点建设国际化街区   

                                                  text  \
0    　　■ 2022年，我们胜利召开党的二十大，擘画了全面建设社会主义现代化国家、以中国式现代化...   
1    　　新华社北京12月31日电  2022年12月31日，国家主席习近平和俄罗斯总统普京互致新...   
2    　　新华社北京12月31日电  2023年1月1日出版的第1期《求是》杂志将发表中共中央总书...   
3    　　新华社北京12月31日电  12月31日，中共中央总书记习近平致电祝贺拉马福萨当选连任南...   
4    　　日月开新元，

# 3. bertopic基本流程
![0](https://vivounicorn.github.io/images/bertopic/BERTopic.png)

## 3.1使用 BERT 或任何其他嵌入技术提取文档嵌入向量
两种方式:
- 加载词向量字典（如果你没有安装torch和huggingface）
>模型词典地址：https://github.com/Embedding/Chinese-Word-Vectors
- 加载词嵌入模型（列如：bert）


In [6]:
import gensim
from gensim.models import KeyedVectors
# tencent 预训练的词向量文件路径
vec_path = "Pre-trained_Chinese_Word_Vectors/merge_sgns_bigram_char300.txt"
embed_path = "Pre-trained_Chinese_Word_Vectors/merge_sgns_bigram_char300.bin"
# 加载词向量文件
# wv_from_text = gensim.models.KeyedVectors.load_word2vec_format(vec_path, binary=False)

# # 如果每次都用上面的方法加载，速度非常慢，可以将词向量文件保存成bin文件，以后就加载bin文件，速度会变快
# wv_from_text.init_sims(replace=True)
# wv_from_text.save(vec_path.replace(".txt", ".bin"))

# 之后可以用下面的方式加载词向量
# Step 1 - 嵌入文本
wv_from_text = gensim.models.KeyedVectors.load(embed_path, mmap='r')

# 加载嵌入模型
# embedding_model = SentenceTransformer('D:/notebook/BERTopic/all-MiniLM-L6-v2')



## 3.1 向量降维、聚类、构建表征主题

### 使用UMAP对向量降维(同时保留位置信息)
聚类一般是在二维根据进行，而词嵌入得到一般是高维的向量，所以得把高维向量映射到低维空间

### 使用HDBSCAN算法去聚类
也可以用k-means聚类

### 采用c−TF−IDF得到各个主题的主题词
用以评估一字词对于一个语料库中的其中一份文件的重要程度。

字词的重要性随着它在文件中出现的次数成正比增加，但同时会随着它在语料库中出现的频率成反比下降。


**一般来说bertopic会自动完成这些工作,除非你想修改相关参数** 
  * 1.降维部分的参数：
>   - n_neighbors：近似最近邻数。它控制了UMAP局部结构与全局结构的平衡，数值较小时，UMAP会更加关注局部结构，反之，会关注全局结构，丢掉一些细节。
>   - n_components：设置将数据嵌入的降维空间的维数。
>   - min_dist：点之间的最小距离。此参数控制UMAP聚集在一起的紧密程度，值较小时，会更紧密，反之，会更松散。
  *  2.聚类部分的参数：
>   - min_cluster_size：控制集群的最小大小,它通常设置为默认值10。值越大，集群越少但规模更大，而值越小，微集群越多。
>   - metric：用于计算距离,通常使用默认值euclidean.
>   - prediction_data：一般始终将此值设置为True，可以预测新点。如果不进行预测，可以将其设置为False。

In [ ]:
# from umap import UMAP
# from hdbscan import HDBSCAN
# from bertopic.vectorizers import ClassTfidfTransformer
# from sklearn.feature_extraction.text import CountVectorizer
# # Step 2 - 向量降维
# umap_model = UMAP(n_neighbors=15, n_components=5,min_dist=0.0,metric='cosine')

# # Step 3 - 使用聚类
# hdbscan_model = HDBSCAN(min_cluster_size=10, metric='euclidean', prediction_data=True)

# Step 4 - 构建表征主题
# vectorizer_model = CountVectorizer(stop_words="chinese")
# ctfidf_model = ClassTfidfTransformer()

## 3.2 进行BerTopic
使用fit_transform对输入文本向量化，然后使用topic_model模型提取主题topics。

> + 相关参数如下
>  - top_n_words：设置提取的每个主题的字数，通常为10-30之间。
>  - min_topic_size：设置主题最小大小，值越低，创建的主题就越多。值太高，则可能根本不会创建任何主题。
>  - nr_topics：设置主题数量，可以设置为一个具体的数字，也可设置为‘none’不进行主题数量约束，设置为‘auto’则自动进行约束。

In [13]:
from bertopic import BERTopic




topic_model = BERTopic(language="chinese (simplified)",
                       embedding_model=wv_from_text,       # Step 1 - 嵌入文本
#                      embedding_model=embedding_model,    # Step 1 - 使用词嵌入模型
#                      umap_model=umap_model,              # Step 2 - 向量降维
#                      hdbscan_model=hdbscan_model,        # Step 3 - 使用聚类
#                      vectorizer_model=vectorizer_model,  # Step 4 - 将文本转换为词频矩阵
#                      ctfidf_model=ctfidf_model,          # Step 5 - 构建表征主题
                       nr_topics='none',
                       top_n_words = 10,
                       calculate_probabilities=True,
                       verbose=True, )

# 去掉 NaN，并确保所有元素都是字符串
docs = df['content'].dropna().astype(str).tolist() 
topics, probs = topic_model.fit_transform(docs)


2024-10-20 21:52:16,043 - BERTopic - Embedding - Transforming documents to embeddings.
100%|██████████| 924/924 [00:03<00:00, 296.36it/s]
2024-10-20 21:52:19,194 - BERTopic - Embedding - Completed ✓
2024-10-20 21:52:19,195 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-10-20 21:52:23,813 - BERTopic - Dimensionality - Completed ✓
2024-10-20 21:52:23,816 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-10-20 21:52:23,954 - BERTopic - Cluster - Completed ✓
2024-10-20 21:52:23,955 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-10-20 21:52:24,525 - BERTopic - Representation - Completed ✓
2024-10-20 21:52:24,527 - BERTopic - Topic reduction - Reducing number of topics
2024-10-20 21:52:25,101 - BERTopic - Topic reduction - Reduced number of topics from 28 to 18


# 4. 主题文档概率

In [14]:
# 计算主题文档概率probabilities
topic_model.get_document_info(docs)

Document  Topic  \
0    2022 胜利 召开 党 二十大 擘画 全面 建设 社会主义 现代化 国家 中国式 现代化 ...      0   
1    新华社 北京 12 31 日电 2022 12 31 国家 主席 习近平 俄罗斯 总统 普京...      2   
2    新华社 北京 12 31 日电 2023 1 1 出版 1 期求 杂志 发表 中共中央 总书...      0   
3    新华社 北京 12 31 日电 12 31 中共中央 总书记 习近平 致电 祝贺 拉马 福萨...      2   
4    日月 开 新元 万象 启新 篇 告别 2022 迎来 2023 时间 再次 刻印 前行 坐标...      0   
..                                                 ...    ...   
919                             本期 统筹 杨暄 智春丽 版式 设计 蔡华伟     10   
920  核心 阅读 保护 古城 风貌 破解 城市 快速 发展 带来 停车难 问题 苏州 错时 共享 ...     15   
921  本报 北京 1 12 日电 记者 邱超 奕 记者 应急 管理部 获悉 气象部门 预测 受 强...     -1   
922  本报 重庆 1 12 日电 记者 常碧罗 记者 重庆市 民政局 获悉 重庆市政府 近日 出台...     -1   
923  本报 广州 1 12 日电 记者 罗艾桦 近日 广东省 广州市 印发 国际化 街区 试点 建...     -1   

                Name                                Representation  \
0     0_全面_习近平_时代_中国     [全面, 习近平, 时代, 中国, 建设, 工作, 发展, 人民, 政治, 推进]   
1      2_合作_双方_关系_中方      [合作, 双方, 关系, 中方, 总统, 发展, 两国, 中土, 中国, 领域]   
2     0_全面_习近平_时代_中国     [全面, 习近平, 时代, 中国, 建设, 工作, 发展, 人民, 政治, 推进]   
3      2_合作_双方_关系_中方      [合作, 双方, 关系, 中方, 总统, 发展, 两国, 中土, 中国, 领域]   
4     0_全面_习近平_时代_中国     [全面, 习近平, 时代, 中国, 建设, 工作, 发展, 人民, 政治, 推进]   
..               ...                                           ...   
919   10_版式_本版_设计_本期  [版式, 本版, 设计, 本期, 统筹, 张芳曼, 沈亦伶, 张彦春, 董建勤, 制图]   
920  15_停车_停车场_小店_消费   [停车, 停车场, 小店, 消费, 车位, 消费者, 边角料, 南京, 外卖, 喜茶]   
921   -1_发展_中国_服务_企业    [发展, 中国, 服务, 企业, 国家, 2022, 工作, 建设, 疫情, 文化]   
922   -1_发展_中国_服务_企业    [发展, 中国, 服务, 企业, 国家, 2022, 工作, 建设, 疫情, 文化]   
923   -1_发展_中国_服务_企业    [发展, 中国, 服务, 企业, 国家, 2022, 工作, 建设, 疫情, 文化]   

                                   Representative_Docs  \
0    [党 世界 最大 马克思主义 执政党 始终 赢得 人民 拥护 巩固 长期 执政 地位 必须 ...   
1    [一应 中华人民共和国 主席 习近平 邀请 土库曼斯坦 总统 谢尔 达尔 尔德 穆哈 梅 多...   
2    [党 世界 最大 马克思主义 执政党 始终 赢得 人民 拥护 巩固 长期 执政 地位 必须 ...   
3    [一应 中华人民共和国 主席 习近平 邀请 土库曼斯坦 总统 谢尔 达尔 尔德 穆哈 梅 多...   
4    [党 世界 最大 马克思主义 执政党 始终 赢得 人民 拥护 巩固 长期 执政 地位 必须 ...   
..                                                 ...   
919  [本版 统筹 董建勤 张彦春 版式 设计 沈亦伶 汪哲平, 本版 统筹 董建勤 张彦春 版式...   
920  [习近平 总书记 党 二十大 报告 指出 采取 惠民 生暖 民心 举措 着力 解决 人民 群...   
921  [新年伊始 一股 复苏 力量 悄然 涌动 早晚 高峰 北京 东三环 国贸 桥 堵车 地铁 车...   
922  [新年伊始 一股 复苏 力量 悄然 涌动 早晚 高峰 北京 东三环 国贸 桥 堵车 地铁 车...   
923  [新年伊始 一股 复苏 力量 悄然 涌动 早晚 高峰 北京 东三环 国贸 桥 堵车 地铁 车...   

                                           Top_n_words  Probability  \
0     全面 - 习近平 - 时代 - 中国 - 建设 - 工作 - 发展 - 人民 - 政治 - 推进     0.905389   
1      合作 - 双方 - 关系 - 中方 - 总统 - 发展 - 两国 - 中土 - 中国 - 领域     0.432563   
2     全面 - 习近平 - 时代 - 中国 - 建设 - 工作 - 发展 - 人民 - 政治 - 推进     1.000000   
3      合作 - 双方 - 关系 - 中方 - 总统 - 发展 - 两国 - 中土 - 中国 - 领域     0.790252   
4     全面 - 习近平 - 时代 - 中国 - 建设 - 工作 - 发展 - 人民 - 政治 - 推进     1.000000   
..                                                 ...          ...   
919  版式 - 本版 - 设计 - 本期 - 统筹 - 张芳曼 - 沈亦伶 - 张彦春 - 董建勤...     1.000000   
920  停车 - 停车场 - 小店 - 消费 - 车位 - 消费者 - 边角料 - 南京 - 外卖 ...     1.000000   
921  发展 - 中国 - 服务 - 企业 - 国家 - 2022 - 工作 - 建设 - 疫情 - 文化     0.567652   
922  发展 - 中国 - 服务 - 企业 - 国家 - 2022 - 工作 - 建设 - 疫情 - 文化     0.438387   
923  发展 - 中国 - 服务 - 企业 - 国家 - 2022 - 工作 - 建设 - 疫情 - 文化     0.457989   

     Representative_document  
0                      False  
1                      False  
2                      False  
3                      False  
4                      False  
..                       ...  
919                    False  
920                    False  
921                    False  
922                    False  
923                    False  

[924 rows x 8 columns]

In [15]:
# 查看每个主题数量，其中-1为噪声，没有聚到任何一类中。
topic_model.get_topic_freq()

Topic  Count
2      -1    281
0       0    243
4       1     81
1       2     57
5       3     43
10      4     28
14      5     27
7       6     21
16      7     18
9       8     17
17      9     17
6      10     16
8      11     13
11     12     13
15     13     13
3      14     13
13     15     12
12     16     11

In [16]:
# 查看某个主题-词的概率分布，这里是第1篇新闻的c-TF-IDF的结果
topic_model.get_topic(0)

[('全面', 0.018454131608295066),
 ('习近平', 0.01750658818650768),
 ('时代', 0.016956701061101982),
 ('中国', 0.01662353254604759),
 ('建设', 0.016286593286243788),
 ('工作', 0.01534484279425237),
 ('发展', 0.014670230632600211),
 ('人民', 0.014472776830758127),
 ('政治', 0.014178695230000163),
 ('推进', 0.012957284922354617)]

# 5. BERTopic可视化
BERTopic还提供了丰富的可视化工具，可以帮助您理解生成的主题。

## 5.1 主题-词概率分布

In [17]:
topic_model.visualize_barchart()

## 5.2 文档主题聚类
展示文档在主题空间中的分布情况，通常用于观察不同文档之间的关系和主题的分布。
每个点在图中的位置表示文档在主题空间中的特征，距离较近的点通常表示文档之间的主题相似度较高。

In [20]:
topic_model.visualize_documents(docs, embeddings=wv_from_text)

## 5.3 聚类分层
主题之间的连接线表示它们的相似性或关系，通常较相似的主题会被组织在一起，形成一个树状结构或分层结构。

In [21]:
topic_model.visualize_hierarchy()

## 5.4 主题相似度热力图

In [22]:
topic_model.visualize_heatmap()

## 5.5 隐含主题主题分布图
>- 图中每个点代表一个主题。
> - 点之间的距离表示主题之间的相似性。距离越近，主题越相似，反之亦然。
> - 点的大小表示该主题在文档集合中的重要性，通常与该主题下文档的数量或频率相关。

In [23]:
topic_model.visualize_topics()